<a href="https://colab.research.google.com/github/Mansiraj1309/Mansiraj1309/blob/main/Image_captioning_in_hindi.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install torch torchvision torchaudio transformers nltk fastai --quiet


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 4.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 59.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 52.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 36.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 6.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 13.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 8.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 5.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 45.0 MB/s eta 0:00:00


In [1]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

import os

from fastai.vision.all import *
from fastai.text.all import *
from pathlib import Path

import torch
import torch.nn.functional as F
import torch.optim as optim
from torch.nn.utils.rnn import pad_sequence
from torch.utils.data import DataLoader, Dataset
from torch.utils.data.sampler import SubsetRandomSampler
import torchvision

import nltk
nltk.download('punkt')
from nltk.tokenize import word_tokenize # for tokenization
from collections import Counter     # for tokenizer

import torchvision.transforms as T
import torchvision.models as models

import matplotlib.pyplot as plt
# import matplotlib.image as Image
import PIL
from PIL import Image
# for the bleu scores
from nltk.translate import bleu
from nltk.translate.bleu_score import sentence_bleu
from nltk.translate.bleu_score import corpus_bleu

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


In [2]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
device

device(type='cpu')

In [3]:
from google.colab import drive
drive.mount('/content/drive')

# Path to your ZIP file in Drive
zip_file = "/content/drive/MyDrive/ezyzip.zip"

# Extract it
!unzip -q "$zip_file" -d "/content/extracted_data"


Mounted at /content/drive


In [4]:
images_path = "/content/extracted_data/Images/"
captions_path = "/content/extracted_data/UnClean-5Sentences_withComma.txt"

# Example: Read a CSV file (if exists)
import pandas as pd
df = pd.read_csv(captions_path)
print(df.head())


                                                                                            image,caption
0  1000268201_693b08cb0e,गुलाबी पोशाक में एक बच्चा प्रवेश के रास्ते में सीढ़ियों के एक सेट पर चढ़ रहा है।
1                                            1000268201_693b08cb0e,एक लड़की लकड़ी की इमारत में जा रही है।
2                                       1000268201_693b08cb0e,एक छोटी लड़की लकड़ी के प्लेहाउस में चढ़ गई।
3                           1000268201_693b08cb0e,एक छोटी सी लड़की अपने प्लेहाउस में सीढ़ियाँ चढ़ रही थी।
4                1000268201_693b08cb0e,एक गुलाबी पोशाक में एक छोटी लड़की एक लकड़ी के केबिन में जा रही है।


In [5]:
import os

# List files in the extracted folder
os.listdir("/content/extracted_data")


['~$Clean-5Sentences_withComma.txt',
 'Images ',
 '.DS_Store',
 '~$ean-5Sentences_withComma.txt',
 'UnClean-5Sentences_withComma.txt']

In [6]:
images_path = "/content/extracted_data/Images/"
captions_path = "/content/extracted_data/UnClean-5Sentences_withComma.txt"

# Example: Read a CSV file (if exists)
import pandas as pd
df = pd.read_csv(captions_path)
print(df.head())


                                                                                            image,caption
0  1000268201_693b08cb0e,गुलाबी पोशाक में एक बच्चा प्रवेश के रास्ते में सीढ़ियों के एक सेट पर चढ़ रहा है।
1                                            1000268201_693b08cb0e,एक लड़की लकड़ी की इमारत में जा रही है।
2                                       1000268201_693b08cb0e,एक छोटी लड़की लकड़ी के प्लेहाउस में चढ़ गई।
3                           1000268201_693b08cb0e,एक छोटी सी लड़की अपने प्लेहाउस में सीढ़ियाँ चढ़ रही थी।
4                1000268201_693b08cb0e,एक गुलाबी पोशाक में एक छोटी लड़की एक लकड़ी के केबिन में जा रही है।


In [7]:
class my_dictionary(dict):

    # __init__ function
    def __init__(self):
        self = dict()

    # Function to add key:value
    def add(self, key, value):
        if key not in self.keys():
            self[key] = [value]
        else:
            self[key].append(value)

descriptors = my_dictionary()


In [13]:
!pip install indic-nlp-library
from indicnlp.tokenize import indic_tokenize

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 40.3/40.3 kB 1.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.7/7.7 MB 59.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 121.1/121.1 kB 8.5 MB/s eta 0:00:00


In [20]:
import nltk
nltk.download('punkt_tab') # Download the punkt_tab data for tokenization

images_path = "/content/extracted_data/Images/"
captions_path = "/content/extracted_data/UnClean-5Sentences_withComma.txt"

# Example: Read a CSV file (if exists)
import pandas as pd
# The original code assumes a tab as the delimiter.
# If your data has a different delimiter (e.g., comma),
# specify it using the `sep` argument:
# df = pd.read_csv(captions_path, sep='\t')  # Replace '\t' with the actual delimiter if it's not a tab

# Try using comma as the delimiter since the file name suggests it
df = pd.read_csv(captions_path, sep=',') # Changed sep to ',' assuming comma separated values
print(df.head())

for i in range(len(df)):
    img_id = str(df.iloc[i, 0]) + ".jpg"
    # Assuming the captions are now in the second column (index 1)
    # If there's only one column, change the index to 0

    # Check the number of columns in the DataFrame
    num_cols = df.shape[1]

    # Access the caption column based on the number of columns
    caption_index = 1 if num_cols > 1 else 0

    sentence = ["<start>"] + word_tokenize(str(df.iloc[i, caption_index])) + ["<end>"]

    descriptors.add(img_id, sentence)

[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!


                                                                                            image,caption
0  1000268201_693b08cb0e,गुलाबी पोशाक में एक बच्चा प्रवेश के रास्ते में सीढ़ियों के एक सेट पर चढ़ रहा है।
1                                            1000268201_693b08cb0e,एक लड़की लकड़ी की इमारत में जा रही है।
2                                       1000268201_693b08cb0e,एक छोटी लड़की लकड़ी के प्लेहाउस में चढ़ गई।
3                           1000268201_693b08cb0e,एक छोटी सी लड़की अपने प्लेहाउस में सीढ़ियाँ चढ़ रही थी।
4                1000268201_693b08cb0e,एक गुलाबी पोशाक में एक छोटी लड़की एक लकड़ी के केबिन में जा रही है।


In [21]:
print(descriptors.keys())



dict_keys(['1000268201_693b08cb0e,गुलाबी पोशाक में एक बच्चा प्रवेश के रास्ते में सीढ़ियों के एक सेट पर चढ़ रहा है।.jpg', '1000268201_693b08cb0e,एक लड़की लकड़ी की इमारत में जा रही है।.jpg', '1000268201_693b08cb0e,एक छोटी लड़की लकड़ी के प्लेहाउस में चढ़ गई।.jpg', '1000268201_693b08cb0e,एक छोटी सी लड़की अपने प्लेहाउस में सीढ़ियाँ चढ़ रही थी।.jpg', '1000268201_693b08cb0e,एक गुलाबी पोशाक में एक छोटी लड़की एक लकड़ी के केबिन में जा रही है।.jpg', '1001773457_577c3a7d70,एक काला कुत्ता और एक चित्तीदार कुत्ता लड़ रहे हैं.jpg', '1001773457_577c3a7d70,एक काला कुत्ता और सड़क पर एक दूसरे के साथ खेलता हुआ एक तिरंगा कुत्ता।.jpg', '1001773457_577c3a7d70,एक काले कुत्ते और भूरे रंग के धब्बे वाला एक सफेद कुत्ता सड़क पर एक दूसरे को घूर रहा है।.jpg', '1001773457_577c3a7d70,सड़क पर एक-दूसरे को देख अलग-अलग नस्लों के दो कुत्ते।.jpg', '1001773457_577c3a7d70,फुटपाथ पर दो कुत्ते एक दूसरे की ओर बढ़ते हुए।.jpg', '1002674143_1b742ab4b8,पेंट में ढकी एक छोटी लड़की एक कटोरे में अपने हाथों से चित्रित इंद्रधनुष के सामने ब

In [40]:
os.listdir("/content/extracted_data")


['~$Clean-5Sentences_withComma.txt',
 'Images ',
 '.DS_Store',
 '~$ean-5Sentences_withComma.txt',
 'UnClean-5Sentences_withComma.txt']

In [41]:
import pandas as pd

captions_path = "/content/extracted_data/UnClean-5Sentences_withComma.txt"  # Change this if necessary
df = pd.read_csv(captions_path)

print("Columns in CSV:", df.columns)
print(df.head())  # Check first few rows


Columns in CSV: Index(['image,caption'], dtype='object')
                                                                                            image,caption
0  1000268201_693b08cb0e,गुलाबी पोशाक में एक बच्चा प्रवेश के रास्ते में सीढ़ियों के एक सेट पर चढ़ रहा है।
1                                            1000268201_693b08cb0e,एक लड़की लकड़ी की इमारत में जा रही है।
2                                       1000268201_693b08cb0e,एक छोटी लड़की लकड़ी के प्लेहाउस में चढ़ गई।
3                           1000268201_693b08cb0e,एक छोटी सी लड़की अपने प्लेहाउस में सीढ़ियाँ चढ़ रही थी।
4                1000268201_693b08cb0e,एक गुलाबी पोशाक में एक छोटी लड़की एक लकड़ी के केबिन में जा रही है।


In [42]:
images_path = "/content/extracted_data/Images/"


In [44]:
df = pd.read_csv(captions_path, delimiter=",")  # Adjust delimiter if needed


In [45]:
import zipfile
import os

zip_file = "/content/ezyzip.zip"  # Change this to your ZIP filename
extract_path = "/content/extracted_data"

with zipfile.ZipFile(zip_file, 'r') as zip_ref:
    zip_ref.extractall(extract_path)

print("Files extracted to:", extract_path)

# Set the correct path
captions_path = "/content/extracted_data/UnClean-5Sentences_withComma.txt"
images_path = "/content/extracted_data/Images/"


FileNotFoundError: [Errno 2] No such file or directory: '/content/ezyzip.zip'

In [46]:
# Ensure image_id only contains the filename, not extra text
image_id = str(df.iloc[i, 0]).split(",")[0] + ".jpg"  # Keep only the first part before a comma
image_path = os.path.join(images_path, image_id)


In [47]:
import os
from PIL import Image
import matplotlib.pyplot as plt

# Ensure image_id is correct
image_id = str(df.iloc[i, 0]).split(",")[0] + ".jpg"
image_path = os.path.join(images_path, image_id)

# Check if file exists before opening
if os.path.exists(image_path):
    img = Image.open(image_path)
    plt.imshow(img)
    plt.show()
else:
    print(f"Error: File {image_path} not found!")


Error: File /content/extracted_data/Images/1000268201_693b08cb0e.jpg not found!


In [43]:
from PIL import Image
import matplotlib.pyplot as plt

image_id = df.iloc[0, 0] + ".jpg"  # Get first image filename
image_path = os.path.join(images_path, image_id)

img = Image.open(image_path)
plt.imshow(img)
plt.show()


FileNotFoundError: [Errno 2] No such file or directory: '/content/extracted_data/Images/1000268201_693b08cb0e,गुलाबी पोशाक में एक बच्चा प्रवेश के रास्ते में सीढ़ियों के एक सेट पर चढ़ रहा है।.jpg'

In [ ]:
images_path = "/content/extracted_data/Images/"
captions_path = "/content/extracted_data/UnClean-5Sentences_withComma.txt"

In [39]:
images_path = "/content/extracted_data/Images" # removed the trailing /
import os

# ✅ Use images_path instead of captions_path
files = os.listdir(images_path)
print("Extracted Files:", files)

FileNotFoundError: [Errno 2] No such file or directory: '/content/extracted_data/Images'

In [34]:
import pandas as pd
import nltk
nltk.download('punkt')
from nltk.tokenize import word_tokenize

# ✅ Step 1: Load Data & Ensure Correct Columns
df = pd.read_csv("UnClean-5Sentences_withComma.csv")  # Change filename if needed

# ✅ Step 2: Check if DataFrame Has the Right Columns
print(df.columns)  # Check column names
print(df.shape)  # Check number of columns

# ✅ Step 3: Fix Column Names if Needed
if df.shape[1] == 1:  # Only 1 column found
    df = pd.read_csv("UnClean-5Sentences_withComma.csv", header=None)  # Read without header
    df.columns = ["image_id", "caption"]  # Rename columns

# ✅ Step 4: Process Data Safely
for i in range(len(df)):
    img_id = str(df.iloc[i]["image_id"]) + ".jpg"  # Ensure correct column name
    sentence = ["<start>"] + word_tokenize(str(df.iloc[i]["caption"])) + ["<end>"]
    descriptors.add(img_id, sentence)

print("Processing complete ✅")


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


FileNotFoundError: [Errno 2] No such file or directory: 'UnClean-5Sentences_withComma.csv'

In [30]:
import nltk
nltk.download('punkt')
from nltk.tokenize import word_tokenize

for i in range(len(df)):
    img_id = str(df.iloc[i, 0]) + ".jpg"  # Ensure image ID is a string
    sentence = ["<start>"] + word_tokenize(str(df.iloc[i, 1])) + ["<end>"]  # Tokenize Hindi text

    descriptors.add(img_id, sentence)


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


IndexError: index 1 is out of bounds for axis 0 with size 1

In [27]:
image_indx = 20
# Extract the image ID and clean it (remove potential commas)
image_id = str(df.iloc[image_indx, 0]).replace(',', '')
image_path = os.path.join(images_path, image_id + '.jpg') # Use os.path.join to create the path

# read the image
img = Image.open(image_path)
plt.imshow(img)
plt.show()

# print the captions related to this image
for i in range(image_indx, image_indx+1):
    print(df.iloc[i, 1])

FileNotFoundError: [Errno 2] No such file or directory: '/content/extracted_data/Images/1007129816_e794419615एक नारंगी टोपी में एक आदमी कुछ पर अभिनीत।.jpg'